In [1]:
import sys
sys.path.append("../src/")
sys.path.append("../model/")
sys.path.append("../src/UDA")

In [2]:
from argparse import Namespace

import numpy as np
import torch

from io_utils import load_dataset, model_log
from metric import performance_logloss, performance_pr_auc
from train_utils import reduce_dataset

from labelshift_correction import build_pivot_dataset

from UDA.trainer import *

In [ ]:
task = "kaggle" 
data_type = "cate" 
model_type = "toalign"
version = "opt" 
period = [0, 1, 2, 3] 
source_domain = "source"
target_domain = "target"

In [3]:
cfg = Namespace()

cfg.MODEL = Namespace()
cfg.DATASET = Namespace()
cfg.TRAIN = Namespace()
cfg.METHOD = Namespace()
cfg.OPTIM = Namespace()

cfg.METHOD.HDA = Namespace()

cfg.WORKERS = 5

cfg.MODEL.BASENET = "EmbedNN"
cfg.MODEL.DNET = 'Discriminator'

cfg.MODEL.EMBED_INPUT = [3, 131, 4, 483, 103, 5, 106, 4]
cfg.MODEL.EMBED_DIM = [1, 3, 1, 4, 3, 1, 3, 1]
cfg.MODEL.NUM_DIM = 43

cfg.MODEL.D_HIDDEN_SIZE = 32
cfg.MODEL.D_OUTDIM = 1

cfg.DATASET.NUM_CLASSES = 2

cfg.TRAIN.TTL_ITE = 10000
cfg.TRAIN.PRINT_FREQ = 16
cfg.TRAIN.OUTPUT_CKPT = "./"

cfg.METHOD.ENT = True
cfg.METHOD.W_ALG = 1.0
cfg.METHOD.HDA.LR_MULT = 1.0



cfg.TRAIN.BATCH_SIZE = 4096

cfg.TRAIN.TEST_SIZE = 0.25
cfg.TRAIN.TEST_FREQ = 50
cfg.TRAIN.CATE_INDEX = 8

cfg.OPTIM.MOMENTUM = 0.9
cfg.OPTIM.WEIGHT_DECAY = 5e-4


In [ ]:
mean_perfs = []
for lr in [0.0005,0.0007,0.001]:
    cfg.TRAIN.LR = lr
    perfs = []
    for p in [1,2,3]:
        torch.manual_seed(0)
        np.random.seed(0)

        source_train, source_train_label, source_test, source_test_label = load_dataset("../data/", 
                                                                                        task, source_domain, data_type, p)
        target_train, target_train_label, target_test, target_test_label = load_dataset("../data/", 
                                                                                        task, target_domain, data_type, p)

        # get target_factor and source_factor
        target_factor = (target_train_label[:, 1]==0).sum() / target_train_label[:, 1].sum()
        source_factor = (source_train_label[:, 1]==0).sum() / source_train_label[:, 1].sum()

        # adjusting source train dataset
        source_train, source_train_label, source_index = build_pivot_dataset(
            source_train, source_train_label[:,1], target_factor, source_factor)


        source_index, target_index = reduce_dataset(source_train, target_train)

        cfg.TRAIN.SOURCE_INPUT = source_train[source_index]
        cfg.TRAIN.SOURCE_OUTPUT = source_train_label[source_index, 1]
        cfg.TRAIN.TARGET_INPUT = target_train[target_index]

        model = ToAlign(cfg)
        model.train()


        # source prediction
        pred = model.predict(source_test)

        perf = performance_pr_auc(pred, source_test_label[:, 1])
        print("Source Prediction pr_auc:", perf, flush=True)

        perfs.append(perf)
    mean_perfs.append(np.array(perfs).mean())

In [9]:
cfg.TRAIN.LR = 0.001

for p in [1,2,3]:
    for seed in range(10):
        print("Period", p, "Seed", seed, flush=True)
        torch.manual_seed(seed)
        np.random.seed(seed)

        source_train, source_train_label, source_test, source_test_label = load_dataset("../data/", 
                                                                                        task, source_domain, data_type, p)
        target_train, target_train_label, target_test, target_test_label = load_dataset("../data/", 
                                                                                        task, target_domain, data_type, p)

        # get target_factor and source_factor
        target_factor = (target_train_label[:, 1]==0).sum() / target_train_label[:, 1].sum()
        source_factor = (source_train_label[:, 1]==0).sum() / source_train_label[:, 1].sum()

        # adjusting source train dataset
        source_train, source_train_label, source_index = build_pivot_dataset(
            source_train, source_train_label[:,1], target_factor, source_factor)


        source_index, target_index = reduce_dataset(source_train, target_train)

        cfg.TRAIN.SOURCE_INPUT = source_train[source_index]
        cfg.TRAIN.SOURCE_OUTPUT = source_train_label[source_index, 1]
        cfg.TRAIN.TARGET_INPUT = target_train[target_index]

        model = ToAlign(cfg)
        model.train()


        # source prediction
        pred = model.predict(source_test)

        perf = performance_logloss(pred, source_test_label[:, 1])
        print("Source Prediction logloss:", perf, flush=True)
        model_log("../logs/logloss", task, source_domain, "nn", p, version, 
                     "source_{}: {}".format(model_type, perf))

        perf = performance_pr_auc(pred, source_test_label[:, 1])
        print("Source Prediction pr_auc:", perf, flush=True)
        model_log("../logs/pr_auc", task, source_domain, "nn", p, version, 
                     "source_{}: {}".format(model_type, perf))


        # target prediction
        pred = model.predict(target_test)

        perf = performance_logloss(pred, target_test_label[:, 1])
        print("Target Prediction logloss:", perf, flush=True)
        model_log("../logs/logloss", task, source_domain, "nn", p, version, 
                     "target_{}: {}".format(model_type, perf))

        perf = performance_pr_auc(pred, target_test_label[:, 1])
        print("Target Prediction pr_auc:", perf, flush=True)
        model_log("../logs/pr_auc", task, source_domain, "nn", p, version, 
                     "target_{}: {}".format(model_type, perf))

Period 1 Seed 0
INFO:root:building dataset
INFO:root:source train example length: 11/4
INFO:root:target train example length: 11/4
INFO:root:--> building models: EmbedNN
INFO:root:I:  0/10000 | lr: 0.00100 | l_cls_src: 1.793 | l_alg: 0.691 | l_hda: 0.882 | l_ttl: 3.367 | ent_tar: 0.431 | best_neg_loss: -inf 
INFO:root:I:  16/10000 | lr: 0.00099 | l_cls_src: 0.337 | l_alg: 0.733 | l_hda: 0.100 | l_ttl: 1.170 | ent_tar: 0.522 | best_neg_loss: -inf 
INFO:root:I:  32/10000 | lr: 0.00098 | l_cls_src: 0.240 | l_alg: 0.725 | l_hda: 0.049 | l_ttl: 1.014 | ent_tar: 0.298 | best_neg_loss: -inf 
INFO:root:I:  48/10000 | lr: 0.00097 | l_cls_src: 0.233 | l_alg: 0.712 | l_hda: 0.034 | l_ttl: 0.979 | ent_tar: 0.224 | best_neg_loss: -inf 
INFO:root:--> testing on source_test
INFO:root:I:  49/10000 | src_acc: -0.240 |best_neg_loss: -0.240
INFO:root:    models saved to ./models-last.pt
INFO:root:    keys: dict_keys(['optimizer', 'ite', 'best_neg_loss', 'base_net', 'd_net'])
INFO:root:    best models sav

../src/UDA/trainer/base_trainer.py:249: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  res.append(F.softmax(outputs_all[1]).detach())


Target Prediction logloss: -0.1596393419187132
Target Prediction pr_auc: 0.6427702874261947
Period 1 Seed 1


../src/UDA/trainer/base_trainer.py:249: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  res.append(F.softmax(outputs_all[1]).detach())


INFO:root:building dataset
INFO:root:source train example length: 11/4
INFO:root:target train example length: 11/4
INFO:root:--> building models: EmbedNN
INFO:root:I:  0/10000 | lr: 0.00100 | l_cls_src: 0.399 | l_alg: 1.402 | l_hda: 0.549 | l_ttl: 2.351 | ent_tar: 0.595 | best_neg_loss: -inf 
INFO:root:I:  16/10000 | lr: 0.00099 | l_cls_src: 0.239 | l_alg: 0.818 | l_hda: 0.074 | l_ttl: 1.131 | ent_tar: 0.308 | best_neg_loss: -inf 
INFO:root:I:  32/10000 | lr: 0.00098 | l_cls_src: 0.250 | l_alg: 0.731 | l_hda: 0.084 | l_ttl: 1.064 | ent_tar: 0.185 | best_neg_loss: -inf 
INFO:root:I:  48/10000 | lr: 0.00097 | l_cls_src: 0.240 | l_alg: 0.707 | l_hda: 0.060 | l_ttl: 1.006 | ent_tar: 0.251 | best_neg_loss: -inf 
INFO:root:--> testing on source_test
INFO:root:I:  49/10000 | src_acc: -0.241 |best_neg_loss: -0.241
INFO:root:    models saved to ./models-last.pt
INFO:root:    keys: dict_keys(['optimizer', 'ite', 'best_neg_loss', 'base_net', 'd_net'])
INFO:root:    best models saved to ./models-b

...

../src/UDA/trainer/base_trainer.py:249: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  res.append(F.softmax(outputs_all[1]).detach())


INFO:root:building dataset
INFO:root:source train example length: 11/4
INFO:root:target train example length: 11/4
INFO:root:--> building models: EmbedNN
INFO:root:I:  0/10000 | lr: 0.00100 | l_cls_src: 1.417 | l_alg: 0.911 | l_hda: 0.602 | l_ttl: 2.931 | ent_tar: 0.543 | best_neg_loss: -inf 
INFO:root:I:  16/10000 | lr: 0.00099 | l_cls_src: 0.278 | l_alg: 0.754 | l_hda: 0.084 | l_ttl: 1.115 | ent_tar: 0.357 | best_neg_loss: -inf 
INFO:root:I:  32/10000 | lr: 0.00098 | l_cls_src: 0.261 | l_alg: 0.719 | l_hda: 0.058 | l_ttl: 1.037 | ent_tar: 0.207 | best_neg_loss: -inf 
INFO:root:I:  48/10000 | lr: 0.00097 | l_cls_src: 0.252 | l_alg: 0.704 | l_hda: 0.059 | l_ttl: 1.015 | ent_tar: 0.259 | best_neg_loss: -inf 
INFO:root:--> testing on source_test
INFO:root:I:  49/10000 | src_acc: -0.241 |best_neg_loss: -0.241
INFO:root:    models saved to ./models-last.pt
INFO:root:    keys: dict_keys(['optimizer', 'ite', 'best_neg_loss', 'base_net', 'd_net'])
INFO:root:    best models saved to ./models-b

../src/UDA/trainer/base_trainer.py:249: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  res.append(F.softmax(outputs_all[1]).detach())


Target Prediction logloss: -0.1562299208518378
Target Prediction pr_auc: 0.6374318883648931


../src/UDA/trainer/base_trainer.py:249: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  res.append(F.softmax(outputs_all[1]).detach())
